## Import libraries

In [5]:
import requests
import json
import pandas as pd
import numpy as np
import plotly
import plotly.graph_objects as go
import plotly.express as px
from plotly.offline import plot

In [ ]:
from platform import python_version

print(python_version())

## Unpickle .pkl file back to dataframe

In [12]:
#Raw data
#data = pd.read_pickle("sources/df_articles.pkl")
#data = pd.read_pickle("sources/df_length_of_articles.pkl")

#Data after preprocessing
data = pd.read_pickle("sources/df_articles_ap.pkl")

#Data after added non-credible reference
#data = pd.read_pickle("sources/data_credible_sources.pkl")

data.reset_index(inplace = True, drop = True)
data

body  \
0      Šaľa 7. januára 2020 (TASR/HSP/Foto:TASR- Pavo...   
1      Atény 23. apríla 2020 (TASR/HSP/Foto:TASR/AP-P...   
2      Esslingen 5. februára 2018 (TASR/HSP/Foto:TASR...   
3      \nInformační doplněk k hlavnímu proudu\nSource...   
4      Bratislava 24. júla 2020 (HSP/Združenia sloven...   
...                                                  ...   
76773  Hanoj 3. októbra 2018 (TASR/HSP/Foto:TASR/AP/K...   
76774  Bratislava 10. marca 2020 (TASR/HSP/Foto:SITA-...   
76775  Vždy a tak aj pri vzdelaní máte na výber. Buď ...   
76776  Paríž 6. apríla 2019 (TASR/HSP/Foto:TASR/AP-Ra...   
76777  Bratislava 1. mája 2021 (TASR/HSP/Foto:Pixabay...   

                          published_at  \
0      2020-01-07T12:26:43.000000+0100   
1      2020-04-23T06:01:14.000000+0200   
2      2018-02-05T16:46:32.000000+0100   
3      2020-01-14T08:28:39.000000+0100   
4      2020-07-24T09:00:50.000000+0200   
...                                ...   
76773  2018-10-03T19:32:17.000000+0200   
76774  2020-03-10T11:21:09.000000+0100   
76775  2019-12-07T09:40:33.000000+0100   
76776  2019-04-06T16:52:48.000000+0200   
76777  2021-05-01T08:22:20.000000+0200   

                                                raw_body  \
0      <p>Šaľa 7. januára 2020 (TASR/HSP/Foto:TASR- P...   
1      <p>Atény 23. apríla 2020 (TASR/HSP/Foto:TASR/A...   
2      <p>Esslingen 5. februára 2018 (TASR/HSP/Foto:T...   
3      <p><a href="https://prima.iprima.cz/ranni-kavi...   
4      <p><a href="https://www.hlavnespravy.sk/rozhov...   
...                                                  ...   
76773  <p>Hanoj 3. októbra 2018 (TASR/HSP/Foto:TASR/A...   
76774  <p>Bratislava 10. marca 2020 (TASR/HSP/Foto:SI...   
76775  <div>\n\n                <p class="perex"><str...   
76776  <p>Paríž 6. apríla 2019 (TASR/HSP/Foto:TASR/AP...   
76777  <p>Bratislava 1. mája 2021 (TASR/HSP/Foto:Pixa...   

                                                     url          source.name  \
0      https://www.hlavnespravy.sk/kolednici-ziskali-...      hlavnespravy.sk   
1      https://www.hlavnespravy.sk/dvaja-migranti-sa-...      hlavnespravy.sk   
2      https://www.hlavnespravy.sk/v-nemecku-stvorcle...      hlavnespravy.sk   
3      https://slobodnyvysielac.sk/2020/01/14/14-1-20...  slobodnyvysielac.sk   
4      https://slobodnyvysielac.sk/2020/07/24/rozhovo...  slobodnyvysielac.sk   
...                                                  ...                  ...   
76773  https://www.hlavnespravy.sk/novym-vietnamskym-...      hlavnespravy.sk   
76774  https://www.hlavnespravy.sk/miroslav-lajcak-sa...      hlavnespravy.sk   
76775  https://romanhutira.blog.sme.sk/c/522598/skola...               sme.sk   
76776  https://www.hlavnespravy.sk/zastupcovia-zltych...      hlavnespravy.sk   
76777  https://www.hlavnespravy.sk/slovensko-pocita-v...      hlavnespravy.sk   

       source_name_cred  
0                     1  
1                     1  
2                     1  
3                     0  
4                     0  
...                 ...  
76773                 1  
76774                 1  
76775                 1  
76776                 1  
76777                 1  

[76778 rows x 6 columns]

In [ ]:
data_test = data.loc[data['source.name'] == 'hlavnespravy.sk']
data_test

In [10]:
webpages = data['source.name'].unique()

#webpages
#count1 = len(data.loc[(data['source.name']== 'hlavnespravy.sk') & (data['source_name_cred'] == 1),['source.name','source_name_cred']])
#count0 = len(data.loc[(data['source.name']== 'hlavnespravy.sk') & (data['source_name_cred'] == 0),['source.name','source_name_cred']])

d = pd.DataFrame()

for web in webpages:
    count1 = len(data.loc[(data['source.name']== web) & (data['source_name_cred'] == 1),['source.name','source_name_cred']])
    temp = pd.DataFrame(
        {
            'source.name': web,
            'credibility': '1',
            'count': count1
        }, index=[0]
    )

    d = pd.concat([d, temp])
    
for web in webpages:
    count0 = len(data.loc[(data['source.name']== web) & (data['source_name_cred'] == 0),['source.name','source_name_cred']])
    temp = pd.DataFrame(
        {
            'source.name': web,
            'credibility': '0',
            'count': count0
        }, index=[0]
    )

    d = pd.concat([d, temp])    

# Articles by credibility

In [11]:
fig = px.bar(d, x="source.name", y="count", color="credibility", title="Articles by credibility").update_xaxes(categoryorder="total ascending")
fig.show()

## Sum of articles by source_name in ascending order

In [6]:
#fig = px.histogram(data, x="source.name")
fig = px.histogram(data, x='source.name').update_xaxes(categoryorder="total ascending")
fig.show()

## Load konspiratori.sk list

In [7]:
with open('sources/zoznam_konspiratori.txt') as f:
    lines = f.readlines()
   #print(lines)
    
websites = [x.strip() for x in lines] 

## Add column with the value of the credibility from konspiratori.sk list

In [8]:
# NON CREDIBLE = 0
# CREDIBLE = 1
new_column = []
for source_name in data['source.name']:
    #print("hladany web je " + source_name)
    for website in websites:
        #print("porovnavam weby (" + source_name + "," + website + ")")
        if website == source_name:
            score = 0
            #print ("NASIEL SOM")
            break
        else:
            score = 1
    new_column.append(score)
#print(new_column)
data['source_name_cred'] = new_column
print(data[['source.name', 'source_name_cred']])

               source.name  source_name_cred
0          hlavnespravy.sk                 0
1          hlavnespravy.sk                 0
2          hlavnespravy.sk                 0
3      slobodnyvysielac.sk                 0
4      slobodnyvysielac.sk                 0
...                    ...               ...
76773      hlavnespravy.sk                 0
76774      hlavnespravy.sk                 0
76775               sme.sk                 1
76776      hlavnespravy.sk                 0
76777      hlavnespravy.sk                 0

[76778 rows x 2 columns]


## Number of articles by days

In [ ]:
data.reset_index(inplace = True, drop = True)

df = data
df.published_at = pd.to_datetime(df.published_at, format='%Y-%m-%d', utc=True).dt.date
df_by_date = df.iloc[df.published_at.sort_values().index]


articles_by_date = df_by_date.groupby('published_at').published_at.count().reset_index(name="count")
#print(articles_by_date)

fig = px.line(articles_by_date, x='published_at', y='count', title='Articles by days between 2018 and 2021')
fig.show()

## Number of articles by days (Credible news)


In [ ]:
data_credible = data.loc[data['source_name_cred'] == 1]
data_credible.reset_index(inplace = True, drop = True)

df = data_credible
df.published_at = pd.to_datetime(df.published_at, format='%Y-%m-%d', utc=True).dt.date
df_by_date_cred = df.iloc[df.published_at.sort_values().index]


articles_by_date_cred = df_by_date_cred.groupby('published_at').published_at.count().reset_index(name="count")
#print(articles_by_date)

fig = px.line(articles_by_date_cred, x='published_at', y='count', title='Articles by days between 2018 and 2021')
fig.update_traces(line=dict(color="green", width=2))
fig.show()

## Number of articles by days (NonCredible news)


In [ ]:
data_non_credible = data.loc[data['source_name_cred'] == 0]
data_non_credible.reset_index(inplace = True, drop = True)

df = data_non_credible
df.published_at = pd.to_datetime(df.published_at, format='%Y-%m-%d', utc=True).dt.date
df_by_date_cred = df.iloc[df.published_at.sort_values().index]


articles_by_date_cred = df_by_date_cred.groupby('published_at').published_at.count().reset_index(name="count")
#print(articles_by_date)

fig = px.line(articles_by_date_cred, x='published_at', y='count', title='Articles by days between 2018 and 2021')
fig.update_traces(line=dict(color="red", width=2))
fig.show()

## Number of articles by months

In [30]:
data.reset_index(inplace = True, drop = True)

df_month = data
df_month.published_at = pd.to_datetime(df_month.published_at, format='%Y-%m', utc=True).dt.strftime('%Y-%m')
df_by_months = df_month.iloc[df_month.published_at.sort_values().index]

articles_by_months = df_by_months.groupby('published_at').published_at.count().reset_index(name="count")
print('Spolu clankov: {}'.format(articles_by_months['count'].sum()))

fig = px.line(articles_by_months, x='published_at', y='count', title='Articles by months between 2018 and 2021')
fig.update_traces(line=dict(color="green", width=2))
fig.show()

Spolu clankov: 76777


## Number of articles by months (Credible news)

In [52]:
data_credible = data.loc[data['source_name_cred'] == 1]
print(data_credible.loc[(data_credible['published_at'] == '2020-03'),['published_at','source.name', 'source_name_cred']])
data_credible.reset_index(inplace = True, drop = True)

df_month = data_credible
df_month.published_at = pd.to_datetime(df_month.published_at, format='%Y-%m', utc=True).dt.strftime('%Y-%m')
df_by_months = df_month.iloc[df_month.published_at.sort_values().index]

articles_by_months = df_by_months.groupby('published_at').published_at.count().reset_index(name="count")
print('Spolu clankov: {}'.format(articles_by_months['count'].sum()))

fig = px.line(articles_by_months, x='published_at', y='count', title='Articles by months between 2018 and 2021')
fig.update_traces(line=dict(color="blue", width=2))
fig.show()

      published_at      source.name  source_name_cred
43         2020-03  hlavnespravy.sk                 1
104        2020-03  hlavnespravy.sk                 1
152        2020-03          ta3.com                 1
238        2020-03  hlavnespravy.sk                 1
240        2020-03  hlavnespravy.sk                 1
...            ...              ...               ...
76566      2020-03  hlavnespravy.sk                 1
76679      2020-03  hlavnespravy.sk                 1
76753      2020-03  hlavnespravy.sk                 1
76770      2020-03  hlavnespravy.sk                 1
76773      2020-03  hlavnespravy.sk                 1

[2304 rows x 3 columns]
Spolu clankov: 49362


/home/ws16-silhavik/.local/lib/python3.8/site-packages/pandas/core/generic.py:5516: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



## Number of articles by months (Non-Credible news)

In [24]:
data_non_credible = data.loc[data['source_name_cred'] == 0]
data_non_credible.reset_index(inplace = True, drop = True)

df_month = data_non_credible
df_month.published_at = pd.to_datetime(df_month.published_at, format='%Y-%m', utc=True).dt.strftime('%Y-%m')
df_by_months = df_month.iloc[df_month.published_at.sort_values().index]

articles_by_months = df_by_months.groupby('published_at').published_at.count().reset_index(name="count")
print('Spolu clankov: {}'.format(articles_by_months['count'].sum()))

fig = px.line(articles_by_months, x='published_at', y='count', title='Articles by months between 2018 and 2021')
fig.update_traces(line=dict(color="red", width=2))
fig.show()

Spolu clankov: 27415


## Merged both graphs

In [43]:


data1 = data.loc[data['source_name_cred'] == 0]
data2 = data.loc[data['source_name_cred'] == 1]
data1.reset_index(inplace = True, drop = True)
data2.reset_index(inplace = True, drop = True)

df1 = data1
df1.published_at = pd.to_datetime(df1.published_at, format='%Y-%m', utc=True).dt.strftime('%Y-%m')
df_months1 = df1.iloc[df1.published_at.sort_values().index]
by_months1 = df_months1.groupby('published_at').published_at.count().reset_index(name="count")
#print(by_months1)

df2 = data2
df2.published_at = pd.to_datetime(df2.published_at, format='%Y-%m', utc=True).dt.strftime('%Y-%m')
df_months2 = df2.iloc[df2.published_at.sort_values().index]
by_months2 = df_months2.groupby('published_at').published_at.count().reset_index(name="count")
#print(by_months2)

fig1 = px.line(by_months1, x='published_at', y=['count'], title='Articles by months between 2018 and 2021', markers=True)
fig2 = px.line(by_months2, x='published_at', y=['count'], title='Articles by months between 2018 and 2021', markers=True)
#fig.add_line(by_months2, x='published_at', y='count', name="non credible")
fig1.update_traces(line=dict(color="red", width=2), name='non-credible')
fig2.update_traces(line=dict(color="blue", width=2), name='credible')
fig = go.Figure(data = fig1.data + fig2.data)
fig.update_layout(showlegend=True)
fig.show()



In [14]:
data1 = pd.read_pickle("sources/data_credible_sources.pkl")

In [ ]:
data1

In [15]:
df1 = data
df1.published_at = pd.to_datetime(df1.published_at, format='%Y-%m', utc=True).dt.strftime('%Y-%m')
df_months1 = df1.iloc[df1.published_at.sort_values().index]
count_by_months = df_months1.groupby('published_at').published_at.count().reset_index(name="count")

In [16]:
i = df1[df1['published_at'] == '2017-12'].index
df1.drop(i, inplace=True)
df1

published_at                                           raw_body  \
0          2020-01  <p>Šaľa 7. januára 2020 (TASR/HSP/Foto:TASR- P...   
1          2020-04  <p>Atény 23. apríla 2020 (TASR/HSP/Foto:TASR/A...   
2          2018-02  <p>Esslingen 5. februára 2018 (TASR/HSP/Foto:T...   
3          2020-01  <p><a href="https://prima.iprima.cz/ranni-kavi...   
4          2020-07  <p><a href="https://www.hlavnespravy.sk/rozhov...   
...            ...                                                ...   
76773      2018-10  <p>Hanoj 3. októbra 2018 (TASR/HSP/Foto:TASR/A...   
76774      2020-03  <p>Bratislava 10. marca 2020 (TASR/HSP/Foto:SI...   
76775      2019-12  <div>\n\n                <p class="perex"><str...   
76776      2019-04  <p>Paríž 6. apríla 2019 (TASR/HSP/Foto:TASR/AP...   
76777      2021-05  <p>Bratislava 1. mája 2021 (TASR/HSP/Foto:Pixa...   

               source.name  source_name_cred  non_credible_source  
0          hlavnespravy.sk                 1                    0  
1          hlavnespravy.sk                 1                    0  
2          hlavnespravy.sk                 1                    0  
3      slobodnyvysielac.sk                 0                    0  
4      slobodnyvysielac.sk                 0                    1  
...                    ...               ...                  ...  
76773      hlavnespravy.sk                 1                    0  
76774      hlavnespravy.sk                 1                    0  
76775               sme.sk                 1                    0  
76776      hlavnespravy.sk                 1                    0  
76777      hlavnespravy.sk                 1                    0  

[76777 rows x 5 columns]

In [17]:
sorted = df1.sort_values(by='published_at', ascending=True)

In [18]:
sorted_data = sorted['published_at'].value_counts(sort = False)

In [19]:
sorted_data.keys()

Index(['2018-01', '2018-02', '2018-03', '2018-04', '2018-05', '2018-06',
       '2018-07', '2018-08', '2018-09', '2018-10', '2018-11', '2018-12',
       '2019-01', '2019-02', '2019-03', '2019-04', '2019-05', '2019-06',
       '2019-07', '2019-08', '2019-09', '2019-10', '2019-11', '2019-12',
       '2020-01', '2020-02', '2020-03', '2020-04', '2020-05', '2020-06',
       '2020-07', '2020-08', '2020-09', '2020-10', '2020-11', '2020-12',
       '2021-01', '2021-02', '2021-03', '2021-04', '2021-05', '2021-06',
       '2021-07', '2021-08', '2021-09', '2021-10', '2021-11', '2021-12',
       '2022-01', '2022-02', '2022-03'],
      dtype='object')

In [60]:
cols = ['month', 'perc_credible', 'perc_noncredible']
lst = []

for x in sorted_data.keys():
    sorted_months = sorted.loc[sorted['published_at'] == x]
    #print(sorted_months['source_name_cred'].value_counts(sort = False))
    
    credible_month = sorted_months[(sorted_months['source_name_cred'] == 1)]
    non_credible_month = sorted_months[(sorted_months['source_name_cred'] == 0)]
    
    credible_month_with_non_credible_source = sorted_months[(sorted_months['source_name_cred'] == 1) & (sorted_months['non_credible_source'] == 1)]
    non_credible_month_with_non_credible_source = sorted_months[(sorted_months['source_name_cred'] == 0) & (sorted_months['non_credible_source'] == 1)]
    
    print(x)
#     print('All credible monthly articles: {}'.format(len(credible_month)))
#     print('All non-credible monthly articles: {}'.format(len(non_credible_month)))
    
#     print('Credible source with non credible citations: {}'.format(len(credible_month_with_non_credible_source)))
#     print('Non-Credible source with non credible citations: {}'.format(len(non_credible_month_with_non_credible_source)))
    
    if len(credible_month) > 0:
        cred_percentage = (len(credible_month_with_non_credible_source)/len(credible_month))*100
        #print(cred_percentage)
        print('Za mesiac {} bolo {:.2f}% kredibilnych clankov(celkovo {} clankov), ktore odkazovali na nekredibilne zdroje'.format(x, cred_percentage, len(credible_month)))
    else:
        cred_percentage = 0.0
    if len(non_credible_month) > 0:
        non_cred_percentage = (len(non_credible_month_with_non_credible_source)/len(non_credible_month))*100
        #print(non_cred_percentage)
        print('Za mesiac {} bolo {:.2f}% nekredibilnych clankov(celkovo {} clankov), ktore odkazovali na nekredibilne zdroje'.format(x, non_cred_percentage, len(non_credible_month)))
    else:
        non_cred_percentage = 0.0
    print('\n')
    
    lst.append([x, cred_percentage, non_cred_percentage])
    
df1 = pd.DataFrame(lst, columns=cols)
df1    

2018-01
Za mesiac 2018-01 bolo 0.00% kredibilnych clankov(celkovo 541 clankov), ktore odkazovali na nekredibilne zdroje
Za mesiac 2018-01 bolo 22.34% nekredibilnych clankov(celkovo 394 clankov), ktore odkazovali na nekredibilne zdroje


2018-02
Za mesiac 2018-02 bolo 0.00% kredibilnych clankov(celkovo 461 clankov), ktore odkazovali na nekredibilne zdroje
Za mesiac 2018-02 bolo 21.40% nekredibilnych clankov(celkovo 458 clankov), ktore odkazovali na nekredibilne zdroje


2018-03
Za mesiac 2018-03 bolo 0.00% kredibilnych clankov(celkovo 492 clankov), ktore odkazovali na nekredibilne zdroje
Za mesiac 2018-03 bolo 15.97% nekredibilnych clankov(celkovo 689 clankov), ktore odkazovali na nekredibilne zdroje


2018-04
Za mesiac 2018-04 bolo 0.00% kredibilnych clankov(celkovo 486 clankov), ktore odkazovali na nekredibilne zdroje
Za mesiac 2018-04 bolo 22.93% nekredibilnych clankov(celkovo 663 clankov), ktore odkazovali na nekredibilne zdroje


2018-05
Za mesiac 2018-05 bolo 0.20% kredibilnych cl

2021-09
Za mesiac 2021-09 bolo 0.72% kredibilnych clankov(celkovo 1104 clankov), ktore odkazovali na nekredibilne zdroje
Za mesiac 2021-09 bolo 22.89% nekredibilnych clankov(celkovo 402 clankov), ktore odkazovali na nekredibilne zdroje


2021-10
Za mesiac 2021-10 bolo 0.65% kredibilnych clankov(celkovo 463 clankov), ktore odkazovali na nekredibilne zdroje
Za mesiac 2021-10 bolo 14.78% nekredibilnych clankov(celkovo 203 clankov), ktore odkazovali na nekredibilne zdroje


2021-11
Za mesiac 2021-11 bolo 0.26% kredibilnych clankov(celkovo 387 clankov), ktore odkazovali na nekredibilne zdroje
Za mesiac 2021-11 bolo 5.58% nekredibilnych clankov(celkovo 197 clankov), ktore odkazovali na nekredibilne zdroje


2021-12
Za mesiac 2021-12 bolo 0.00% kredibilnych clankov(celkovo 231 clankov), ktore odkazovali na nekredibilne zdroje
Za mesiac 2021-12 bolo 2.98% nekredibilnych clankov(celkovo 235 clankov), ktore odkazovali na nekredibilne zdroje


2022-01
Za mesiac 2022-01 bolo 0.00% kredibilnych cla

month  perc_credible  perc_noncredible
0   2018-01       0.000000         22.335025
1   2018-02       0.000000         21.397380
2   2018-03       0.000000         15.965167
3   2018-04       0.000000         22.926094
4   2018-05       0.200401         26.461988
5   2018-06       0.000000         34.896811
6   2018-07       0.000000         31.778929
7   2018-08       0.000000         24.254473
8   2018-09       0.263158         29.585799
9   2018-10       0.198807         23.003195
10  2018-11       0.000000         21.348315
11  2018-12       0.000000         20.652174
12  2019-01       0.000000         21.370968
13  2019-02       0.184162         19.319938
14  2019-03       0.166113         22.140221
15  2019-04       0.000000         22.487223
16  2019-05       0.000000         41.104972
17  2019-06       0.000000         47.893258
18  2019-07       0.000000         43.577431
19  2019-08       0.000000         45.734266
20  2019-09       0.000000         43.847073
21  2019-10       0.000000         44.513716
22  2019-11       0.000000         41.922563
23  2019-12       0.000000         49.787234
24  2020-01       0.145138         15.682968
25  2020-02       0.140351         29.716981
26  2020-03       0.000000         22.384702
27  2020-04       0.044189         17.107093
28  2020-05       0.095831         17.733990
29  2020-06       0.044563         19.939117
30  2020-07       0.046948         21.915285
31  2020-08       0.370370         15.489130
32  2020-09       0.224048         19.495413
33  2020-10       0.211268         14.446953
34  2020-11       0.280308         20.261438
35  2020-12       0.281294         22.666667
36  2021-01       0.127632         18.800000
37  2021-02       0.475867         17.012448
38  2021-03       0.550796         19.128788
39  2021-04       0.372578         20.119522
40  2021-05       0.373692         26.168224
41  2021-06       0.173010         21.410579
42  2021-07       0.176523         21.311475
43  2021-08       0.198807         22.699387
44  2021-09       0.724638         22.885572
45  2021-10       0.647948         14.778325
46  2021-11       0.258398          5.583756
47  2021-12       0.000000          2.978723
48  2022-01       0.000000          4.782609
49  2022-02       0.467290          4.368932
50  2022-03       0.000000          5.263158

In [64]:
fig1 = px.line(df1, x='month', y='perc_credible', title='Percentage of non-credible sources by months between 2018 and 2021', markers=True)
fig2 = px.line(df1, x='month', y='perc_noncredible', title='Percentage of non-credible sources by months between 2018 and 2021', markers=True)
fig1.update_traces(line=dict(color="blue", width=2), name='non-credible')
fig2.update_traces(line=dict(color="red", width=2), name='credible')

fig = go.Figure(data = fig1.data + fig2.data)
fig.update_layout(showlegend=True)
fig['layout'].update(title = 'Percentuálny pomer citovania nespoľahlivých zdrojov medzi rokmi 2018 až 2022',xaxis_title="výskyt v čase", yaxis_title="percento nespoľahlivých zdrojov", showlegend=True, legend_title_text='test')
fig.show()

In [65]:
print(data_non_credible.loc[(data_non_credible['published_at'] == '2019-12'),['published_at','source.name', 'source_name_cred', 'raw_body', 'non_credible_source']])


      published_at          source.name  source_name_cred  \
36         2019-12      hlavnespravy.sk                 0   
42         2019-12          panobcan.sk                 0   
47         2019-12          panobcan.sk                 0   
151        2019-12  slobodnyvysielac.sk                 0   
178        2019-12          panobcan.sk                 0   
...            ...                  ...               ...   
27294      2019-12       bajecnezeny.sk                 0   
27324      2019-12           somzena.sk                 0   
27356      2019-12          panobcan.sk                 0   
27399      2019-12          panobcan.sk                 0   
27409      2019-12      hlavnespravy.sk                 0   

                                                raw_body  non_credible_source  
36     <p>Bratislava 23. decembra 2019 (HSP/Foto:TASR...                    0  
42     <p>Praha 24. decembra 2019 (SITA/AP/HSP/Foto:P...                    1  
47     <p>Washington 8. dec

In [54]:
data

published_at                                           raw_body  \
0          2020-01  <p>Šaľa 7. januára 2020 (TASR/HSP/Foto:TASR- P...   
1          2020-04  <p>Atény 23. apríla 2020 (TASR/HSP/Foto:TASR/A...   
2          2018-02  <p>Esslingen 5. februára 2018 (TASR/HSP/Foto:T...   
3          2020-01  <p><a href="https://prima.iprima.cz/ranni-kavi...   
4          2020-07  <p><a href="https://www.hlavnespravy.sk/rozhov...   
...            ...                                                ...   
76772      2018-10  <p>Hanoj 3. októbra 2018 (TASR/HSP/Foto:TASR/A...   
76773      2020-03  <p>Bratislava 10. marca 2020 (TASR/HSP/Foto:SI...   
76774      2019-12  <div>\n\n                <p class="perex"><str...   
76775      2019-04  <p>Paríž 6. apríla 2019 (TASR/HSP/Foto:TASR/AP...   
76776      2021-05  <p>Bratislava 1. mája 2021 (TASR/HSP/Foto:Pixa...   

               source.name  source_name_cred  non_credible_source  
0          hlavnespravy.sk                 1                    0  
1          hlavnespravy.sk                 1                    0  
2          hlavnespravy.sk                 1                    0  
3      slobodnyvysielac.sk                 0                    0  
4      slobodnyvysielac.sk                 0                    1  
...                    ...               ...                  ...  
76772      hlavnespravy.sk                 1                    0  
76773      hlavnespravy.sk                 1                    0  
76774               sme.sk                 1                    0  
76775      hlavnespravy.sk                 1                    0  
76776      hlavnespravy.sk                 1                    0  

[76777 rows x 5 columns]

In [94]:
#print(data.loc[(data['source.name'] == 'panobcan.sk'),['published_at','source.name', 'source_name_cred', 'raw_body', 'non_credible_source']])
data_panobcan = (data.loc[(data['source.name'] == 'panobcan.sk'),['raw_body', 'source_name_cred',  'non_credible_source']])
pd.set_option('display.max_rows', None)
data_panobcan

raw_body  source_name_cred  \
12     <p>Biarritz 24. augusta 2019 (TASR/HSP/Foto:SI...                 0   
38     <p>Moskva 23. októbra 2019 (TASR/HSP/Foto:SITA...                 0   
68     <p>Londýn 21. júna 2019 (SITA/AP/HSP/Foto:TASR...                 0   
69     <p>Brusel 29. februára 2020 (TASR/HSP/Foto:TAS...                 0   
117    <p>Naí Dillí 26. júla 2019 (TASR/HSP/Foto:TASR...                 0   
124    <p>Praha 24. decembra 2019 (SITA/AP/HSP/Foto:P...                 0   
130    <p>Washington 8. decembra 2019 (HSP/<span><a h...                 0   
178    <p>Kyjev 18. júna 2019 (HSP/Foto:TASR-Františe...                 0   
231    <p>Bratislava 27. februára 2020 <span>(HSP/Fot...                 0   
324    <p>Kyjev 9. marca 2020 (HSP/<span><a href="htt...                 0   
347    <p>Bratislava 12. novembra 2019 (TASR/HSP/Foto...                 0   
353    <p>Bratislava 20. novembra 2019 (SITA/HSP/Foto...                 0   
424    <p>Kyjev 13. júna 2019 (HSP<span>/<a href="htt...                 0   
483    <p>Poprad 12. októbra 2019 (SITA/HSP/Foto:Pixa...                 0   
488    <p><img src="https://magazin.panobcan.sk/wp-co...                 0   
509    <p>Lyon 31. augusta 2019 (TASR/HSP/Foto:TASR/A...                 0   
524    <p>New York 17. júna 2019 (HSP/Foto:TASR/AP-Pa...                 0   
550    <p>Bratislava 27. mája 2019 AKTUALIZOVANÉ (TAS...                 0   
632    <p>Praha, 04. októbra 2019 (HSP/Foto:TASR-Roma...                 0   
665    <p>Bratislava 20. decembra 2019 (SITA/HSP/Foto...                 0   
684    <p>Bratislava 30. septembra 2019 (TASR/HSP/Fot...                 0   
762    <p><img src="https://magazin.panobcan.sk/wp-co...                 0   
816    <p>Tripolis 21. februára 2020 (HSP/Foto:SITA/A...                 0   
825    <p>Peking/Bratislava 11. júla 2019 (TASR/HSP/F...                 0   
860    <p>Montreal 6. decembra 2019 (TASR/HSP/Foto:SI...                 0   
1015   <p>Bratislava 19. decembra 2019 (SITA/HSP/Foto...                 0   
1071   <p>Peking 20. februára 2020 (HSP/<span><a href...                 0   
1100   <p>Bratislava 10. júna 2019 (HSP/Foto:SITA/AP-...                 0   
1108   <p>Washington 24. augusta 2019 (TASR/HSP/Foto:...                 0   
1146   <p>Bratislava 14. októbra 2019 (TASR/HSP/Foto:...                 0   
1150   <p>Praha 23. februára 2020 <span>(HSP/<a href=...                 0   
1167   <p>Kyjev 31. júla 2019 (TASR/HSP/Foto:<span><a...                 0   
1169   <p>Düsseldorf 13. októbra 2019 (HSP/Foto:Scree...                 0   
1186   <p>Bratislava 2. decembra 2019 AKTUALIZOVANÉ (...                 0   
1219   <p>Hamburg 4. decembra 2019 (HSP/<span><a href...                 0   
1243   <p>Andovce 16. mája 2019 (HSP/Foto:COOP Jednot...                 0   
1258   <h3>Severomorská ropa Brent posilnila</h3>\n<p...                 0   
1262   <p>Alžír 12. decembra 2019 (TASR/HSP/Foto:Maxp...                 0   
1287   <p>Bratislava 17. júna 2019 (SITA/AP/HSP/Foto:...                 0   
1306   <p>Kodaň 20. septembra 2019 (TASR/HSP/Foto:SIT...                 0   
1331   <p>Budapešť 16. februára 2020 AKTUALIZOVANÉ (T...                 0   
1379   <p>Bratislava 7. decembra 2019 (SITA/HSP/Foto:...                 0   
1390   \n<p>Vysoké Tatry 30. apríla 2019 (TASR/HSP/Fo...                 0   
1430   <p>Berlín 1. októbra 2019 (HSP/Foto:SITA/AP-Ev...                 0   
1444   <p>Bratislava 1. júna 2019 (HSP<span>/<a href=...                 0   
1453   <p>Kišiňov 9. júla 2019 (HSP/Foto:TASR/AP-Rove...                 0   
1506   <p>Bratislava 31. júla 2019 (TASR/HSP/Foto:SIT...                 0   
1628   <p>Bratislava 9. augusta2019 (SITA/HSP/Foto:TA...                 0   
1646   <p>Peking 24. júna 2019 (TASR/HSP/Foto:TASR/AP...                 0   
1743   <p><img src="https://magazin.panobcan.sk/wp-co...                 0   
1745   <p>Bratislava/Žiar nad Hronom&nbsp;17. júna 20...              

In [95]:
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)
pd.set_option('display.width', None)

data_panobcan['raw_body'][2254]

'<div><img src="https://magazin.panobcan.sk/wp-content/uploads/2019/07/rusko-ponukalo-ukrajine-predlzenie-dohody-o-tranzite-plynu.jpg" class="ff-og-image-inserted"></div>\n<p class="result-shield-container tlid-copy-target"><span class="tlid-translation translation" lang="sk">Výkonný riaditeľ spoločnosti Naftogaz Jurij Vitrenko uviedol, že Ukrajina sa pripravuje na úplné zastavenie tranzitu po roku 2019.</span></p>\n<p class="result-shield-container tlid-copy-target"><span class="tlid-translation translation" lang="sk">“Musíme, bohužiaľ, očakávať zastavenie tranzitu cez Ukrajinu nielen v prvom štvrťroku 2020, ale vôbec po skončení roka 2019,” napísal Vitrenko na svojom Facebooku.<br /></span></p>\n<p class="result-shield-container tlid-copy-target"><span class="tlid-translation translation" lang="sk">Podľa jeho názoru je pozícia Gazpromu ohľadom zastavenia tranzitu plynu cez územie Ukrajiny podmienená politickými, a nie ekonomickými faktormi. Vitrenko pritom uviedol, že akákoľvek rokov

In [4]:
data

published_at  \
0      2020-01-07T12:26:43.000000+0100   
1      2020-04-23T06:01:14.000000+0200   
2      2018-02-05T16:46:32.000000+0100   
3      2020-01-14T08:28:39.000000+0100   
4      2020-07-24T09:00:50.000000+0200   
...                                ...   
76773  2018-10-03T19:32:17.000000+0200   
76774  2020-03-10T11:21:09.000000+0100   
76775  2019-12-07T09:40:33.000000+0100   
76776  2019-04-06T16:52:48.000000+0200   
76777  2021-05-01T08:22:20.000000+0200   

                                                raw_body          source.name  \
0      <p>Šaľa 7. januára 2020 (TASR/HSP/Foto:TASR- P...      hlavnespravy.sk   
1      <p>Atény 23. apríla 2020 (TASR/HSP/Foto:TASR/A...      hlavnespravy.sk   
2      <p>Esslingen 5. februára 2018 (TASR/HSP/Foto:T...      hlavnespravy.sk   
3      <p><a href="https://prima.iprima.cz/ranni-kavi...  slobodnyvysielac.sk   
4      <p><a href="https://www.hlavnespravy.sk/rozhov...  slobodnyvysielac.sk   
...                                                  ...                  ...   
76773  <p>Hanoj 3. októbra 2018 (TASR/HSP/Foto:TASR/A...      hlavnespravy.sk   
76774  <p>Bratislava 10. marca 2020 (TASR/HSP/Foto:SI...      hlavnespravy.sk   
76775  <div>\n\n                <p class="perex"><str...               sme.sk   
76776  <p>Paríž 6. apríla 2019 (TASR/HSP/Foto:TASR/AP...      hlavnespravy.sk   
76777  <p>Bratislava 1. mája 2021 (TASR/HSP/Foto:Pixa...      hlavnespravy.sk   

       source_name_cred  non_credible_source  
0                     1                    0  
1                     1                    0  
2                     1                    0  
3                     0                    0  
4                     0                    1  
...                 ...                  ...  
76773                 1                    0  
76774                 1                    0  
76775                 1                    0  
76776                 1                    0  
76777                 1                    0  

[76778 rows x 5 columns]